####%pip install google-genai

In [ ]:
from google import genai
import os

assert os.environ.get('GEMINI_API_KEY')
client = genai.Client(api_key=os.environ.get('GEMINI_API_KEY'))

response = client.models.generate_content(model="gemini-2.0-flash", contents="Explain how AI works in a few words")
print(response.text)

AI learns patterns from data to make predictions or decisions.



In [ ]:
MODEL_ID = "gemini-2.0-flash"
from google.genai import types
from IPython.display import Markdown
from pydantic import BaseModel

class Recipe(BaseModel):
    recipe_name: str
    recipe_description: str
    recipe_ingredients: list[str]

response = client.models.generate_content(
    model=MODEL_ID,
    contents="Provide a popular cookie recipe and its ingredients.",
    config=types.GenerateContentConfig(
        response_mime_type="application/json",
        response_schema=Recipe,
    ),
)

Markdown(response.text)

/usr/local/lib/python3.11/site-packages/jedi/inference/compiled/subprocess/functions.py:21: UserWarning: Module _tkinter not importable in path ['/app/data', '/app/solveit', '/usr/local/lib/python311.zip', '/usr/local/lib/python3.11', '/usr/local/lib/python3.11/lib-dynload', '/app/data/.local/lib/python3.11/site-packages', '/usr/local/lib/python3.11/site-packages'].
  return access.load_module(inference_state, **kwargs)


{
  "recipe_name": "Chocolate Chip Cookies",
  "recipe_description": "Classic and delicious chocolate chip cookies, perfect for any occasion.",
  "recipe_ingredients": [
    "1 cup (2 sticks) unsalted butter, softened",
    "3/4 cup granulated sugar",
    "3/4 cup packed brown sugar",
    "2 large eggs",
    "1 teaspoon vanilla extract",
    "2 1/4 cups all-purpose flour",
    "1 teaspoon baking soda",
    "1 teaspoon salt",
    "2 cups chocolate chips"
  ]
}

In [ ]:
# Example meeting transcript
example_transcript = """
Meeting Title: Q4 Product Roadmap Discussion
Date: November 15, 2023
Attendees: Sarah (Product Manager), Michael (Engineering Lead), Priya (UX Designer), Carlos (Marketing), Jennifer (Customer Success)

Sarah: Good morning everyone. Today we need to finalize our Q4 roadmap and prioritize features for the next release.

Michael: Before we dive in, I want to highlight that we're facing some technical debt issues that might slow down new feature development.

Sarah: Thanks for bringing that up. How much time do you think we need to allocate to address those issues?

Michael: I'd say about 30% of our sprint capacity for the next two sprints.

Priya: From the UX perspective, we've completed user testing on the new dashboard design. Users loved the cleaner interface but struggled with finding the export functionality.

Carlos: Marketing needs the new social sharing features by December 10th for our holiday campaign. Is that still feasible?

Michael: If we prioritize it, yes, but we might need to push back the advanced reporting features.

Jennifer: Customer Success team is getting a lot of requests for better notification controls. That should be high priority based on customer feedback.

Sarah: Okay, so it sounds like we have four main items: technical debt, dashboard UX improvements, social sharing, and notification controls.

Michael: That's correct. I suggest we tackle technical debt and notification controls in the first sprint of Q4, then move to dashboard improvements and social sharing in the second sprint.

Priya: That works for me. I can have the final designs for notifications ready by next week.

Carlos: As long as we have social sharing ready by December 10th, marketing is happy.

Jennifer: Perfect. I'll communicate the notification improvements to our key accounts.

Sarah: Great! Let's also schedule a mid-quarter review on November 30th to check our progress. I'll send out the detailed roadmap by end of day tomorrow.

Michael: Sounds good. Any other concerns we should address today?

Priya: Not from the UX team.

Sarah: Alright then, thanks everyone for your input. Let's get to work on making Q4 our best quarter yet!
"""

In [ ]:
# Define a function to summarize meeting transcripts
def summarize_meeting(transcript):
    prompt = f"""
    Please summarize the following meeting transcript, highlighting:
    1. Key discussion points
    2. Decisions made
    3. Action items and owners
    4. Important deadlines mentioned
    
    Please format the summary in a clear, structured way.
    
    Transcript:
    {transcript}
    """
    
    response = client.models.generate_content(
        model="gemini-2.0-flash",
        contents=prompt,
    )
    
    return response.text

# Get the summary
meeting_summary = summarize_meeting(example_transcript)
print(meeting_summary)

## Q4 Product Roadmap Discussion Summary

**Date:** November 15, 2023

**1. Key Discussion Points:**

*   **Technical Debt:** Engineering is facing technical debt issues that will impact feature development velocity.
*   **Dashboard UX:** User testing revealed a positive reaction to the new dashboard design but identified usability issues with the export functionality.
*   **Social Sharing:** Marketing needs social sharing features live by December 10th for the holiday campaign.
*   **Notification Controls:** Customer Success reports high demand for improved notification controls based on customer feedback.
*   **Feature Prioritization:** Balancing technical debt, UX improvements, marketing needs, and customer feedback to determine the Q4 feature roadmap.

**2. Decisions Made:**

*   **Sprint Allocation:** Engineering will dedicate approximately 30% of their sprint capacity for the next two sprints to address technical debt.
*   **Feature Prioritization (Tentative):**
    *   **Sprint 

In [ ]:
from pydantic import BaseModel
from typing import List
from google.genai import types

class ActionItem(BaseModel):
    description: str
    owner: str
    deadline: Optional[str] = None

class MeetingSummary(BaseModel):
    key_points: List[str]
    decisions: List[str]
    action_items: List[ActionItem]
    next_meeting: Optional[str] = None

In [ ]:
def get_structured_summary(transcript):
    prompt = f"""
    Analyze the following meeting transcript and extract:
    
    1. Key discussion points
    2. Decisions made during the meeting
    3. Action items with their owners and deadlines (if mentioned)
    4. The next scheduled meeting date/time (if mentioned)
    
    Format your response as a JSON object matching this structure:
    {{
        "key_points": ["point 1", "point 2", ...],
        "decisions": ["decision 1", "decision 2", ...],
        "action_items": [
            {{"description": "task description", "owner": "person name", "deadline": "date or 'Not specified'"}}
        ],
        "next_meeting": "date/time or 'Not specified'"
    }}
    
    Transcript:
    {transcript}
    """
    
    try:
        response = client.models.generate_content(
            model="gemini-2.0-flash",
            contents=prompt,
            config=types.GenerateContentConfig(
                response_mime_type="application/json",
                response_schema=MeetingSummary,
                temperature=0.1,
            ),
        )
        
        # Parse the response into our Pydantic model
        import json
        summary_dict = json.loads(response.text)
        return MeetingSummary(**summary_dict)
    except Exception as e:
        print(f"Error generating structured summary: {e}")
        return None

In [ ]:
# Get structured summary
structured_summary = get_structured_summary(example_transcript)

if structured_summary:
    print(f"Key Points:")
    for i, point in enumerate(structured_summary.key_points, 1):
        print(f"{i}. {point}")
    
    print(f"\nDecisions:")
    for i, decision in enumerate(structured_summary.decisions, 1):
        print(f"{i}. {decision}")
    
    print(f"\nAction Items:")
    for i, item in enumerate(structured_summary.action_items, 1):
        print(f"{i}. {item.description}")
        print(f"   Owner: {item.owner}")
        print(f"   Deadline: {item.deadline}")
    
    print(f"\nNext Meeting: {structured_summary.next_meeting}")

Key Points:
1. Technical debt issues need to be addressed.
2. User testing on the new dashboard design revealed issues with export functionality.
3. Marketing needs social sharing features by December 10th.
4. Customer Success is receiving requests for better notification controls.
5. Prioritization of technical debt, dashboard UX improvements, social sharing, and notification controls.

Decisions:
1. Tackle technical debt and notification controls in the first sprint of Q4.
2. Move to dashboard improvements and social sharing in the second sprint.
3. Sarah will send out the detailed roadmap by end of day tomorrow.

Action Items:
1. Final designs for notifications
   Owner: Priya
   Deadline: next week
2. Send out detailed roadmap
   Owner: Sarah
   Deadline: tomorrow
3. Communicate the notification improvements to key accounts
   Owner: Jennifer
   Deadline: Not specified

Next Meeting: November 30th
